<a href="https://colab.research.google.com/github/kunai-3txk/Compe_tonyobyo/blob/main/AMP_EDA.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

https://www.kaggle.com/competitions/amp-parkinsons-disease-progression-prediction

# Import Libraries

In [ ]:
#!pip install pandas --upgrade
!pip install pandas-profiling
!pip install --upgrade pandas_profiling

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import pandas_profiling
import os
import xgboost as xgb

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


<ipython-input-1-cd76d1d17729>:8: DeprecationWarning: `import pandas_profiling` is going to be deprecated by April 1st. Please use `import ydata_profiling` instead.
  import pandas_profiling


# Configuration

In [ ]:
class config:
    MAX_PROTEINS = 20
    PROFILE_REPORT = True
    
class paths:
    SAMPLE_SUBMISSION = "/content/drive/MyDrive/AMP/example_test_files/sample_submission.csv"
    SUPPLEMENTAL_CLINICAL_DATA = "/content/drive/MyDrive/AMP/supplemental_clinical_data.csv"
    TRAIN_CLINICAL_DATA = "/content/drive/MyDrive/AMP/train_clinical_data.csv"
    TRAIN_PEPTIDES = "/content/drive/MyDrive/AMP/train_peptides.csv"
    TRAIN_PROTEINS = "/content/drive/MyDrive/AMP/train_proteins.csv"
    TEST_CLINICAL_DATA = "/content/drive/MyDrive/AMP/example_test_files/test.csv"
    TEST_PEPTIDES = "/content/drive/MyDrive/AMP/example_test_files/test_peptides.csv"
    TEST_PROTEINS = "/content/drive/MyDrive/AMP/example_test_files/test_proteins.csv"

# Load Data

train_clinical_data

In [ ]:
train_clinical_data = pd.read_csv(paths.TRAIN_CLINICAL_DATA)
print(f"Train Clinical Dataframe shape has {train_clinical_data.shape[0]} rows and {train_clinical_data.shape[1]} columns")
train_clinical_data.head()

Train Clinical Dataframe shape has 2615 rows and 8 columns


visit_id  patient_id  visit_month  updrs_1  updrs_2  updrs_3  updrs_4  \
0     55_0          55            0     10.0      6.0     15.0      NaN   
1     55_3          55            3     10.0      7.0     25.0      NaN   
2     55_6          55            6      8.0     10.0     34.0      NaN   
3     55_9          55            9      8.0      9.0     30.0      0.0   
4    55_12          55           12     10.0     10.0     41.0      0.0   

  upd23b_clinical_state_on_medication  
0                                 NaN  
1                                 NaN  
2                                 NaN  
3                                  On  
4                                  On

train_peptides

In [ ]:
train_peptides = pd.read_csv(paths.TRAIN_PEPTIDES)
print(f"Train Peptides Dataframe shape has {train_peptides.shape[0]} rows and {train_peptides.shape[1]} columns")
train_peptides.head()

Train Peptides Dataframe shape has 645368 rows and 6 columns


visit_id  visit_month  patient_id UniProt  \
0     55_0            0          55  O00391   
1     55_0            0          55  O00533   
2     55_0            0          55  O00533   
3     55_0            0          55  O00533   
4     55_0            0          55  O00533   

                                  Peptide  PeptideAbundance  
0                           NEQEQPLGQWHLS           11254.3  
1                             GNPEPTFSWTK          102060.0  
2                         IEIPSSVQQVPTIIK          174185.0  
3  KPQSAVYSTGSNGILLC(UniMod_4)EAEGEPQPTIK           27278.9  
4                            SMEQNGPGLEYR           30838.7

train_proteins

In [ ]:
train_proteins = pd.read_csv(paths.TRAIN_PROTEINS)
print(f"Train Proteins Dataframe shape has {train_proteins.shape[0]} rows and {train_proteins.shape[1]} columns")
train_proteins.head()

Train Proteins Dataframe shape has 232741 rows and 5 columns


visit_id  visit_month  patient_id UniProt       NPX
0     55_0            0          55  O00391   11254.3
1     55_0            0          55  O00533  732430.0
2     55_0            0          55  O00584   39585.8
3     55_0            0          55  O14498   41526.9
4     55_0            0          55  O14773   31238.0

supplemental_clinical

In [ ]:
supplemental_clinical_data = pd.read_csv(paths.SUPPLEMENTAL_CLINICAL_DATA)
print(f"Supplemental Clinical Dataframe shape has {supplemental_clinical_data.shape[0]} rows and {supplemental_clinical_data.shape[1]} columns")
supplemental_clinical_data.head()

Supplemental Clinical Dataframe shape has 2223 rows and 8 columns


visit_id  patient_id  visit_month  updrs_1  updrs_2  updrs_3  updrs_4  \
0     35_0          35            0      5.0      3.0     16.0      0.0   
1    35_36          35           36      6.0      4.0     20.0      0.0   
2     75_0          75            0      4.0      6.0     26.0      0.0   
3    75_36          75           36      1.0      8.0     38.0      0.0   
4    155_0         155            0      NaN      NaN      0.0      NaN   

  upd23b_clinical_state_on_medication  
0                                 NaN  
1                                 NaN  
2                                 NaN  
3                                  On  
4                                 NaN

# Focus on each item.

NPX & Abundance (trainPeptide+trainProtein)

In [ ]:
train_ProPep = train_peptides.merge(train_proteins[['visit_id','UniProt','NPX']],on=['visit_id','UniProt'],how='left')
print('shape',train_ProPep.shape)
train_ProPep.head()

shape (645368, 7)


visit_id  visit_month  patient_id UniProt  \
0     55_0            0          55  O00391   
1     55_0            0          55  O00533   
2     55_0            0          55  O00533   
3     55_0            0          55  O00533   
4     55_0            0          55  O00533   

                                  Peptide  PeptideAbundance       NPX  
0                           NEQEQPLGQWHLS           11254.3   11254.3  
1                             GNPEPTFSWTK          102060.0  732430.0  
2                         IEIPSSVQQVPTIIK          174185.0  732430.0  
3  KPQSAVYSTGSNGILLC(UniMod_4)EAEGEPQPTIK           27278.9  732430.0  
4                            SMEQNGPGLEYR           30838.7  732430.0

In [ ]:
#1件だけ欠損 patient_id = 21126
train_ProPep[train_ProPep['NPX'].isnull()==True]
#対象者の全件チェック
train_ProPep[train_ProPep['patient_id']==21126]

visit_id  visit_month  patient_id UniProt  \
52895    21126_0            0       21126  O00391   
52896    21126_0            0       21126  O00533   
52897    21126_0            0       21126  O00533   
52898    21126_0            0       21126  O00533   
52899    21126_0            0       21126  O00533   
...          ...          ...         ...     ...   
645363  21126_36           36       21126  P10909   
645364  21126_36           36       21126  P10909   
645365  21126_36           36       21126  P10909   
645366  21126_36           36       21126  P10909   
645367  21126_36           36       21126      P1   

                                       Peptide  PeptideAbundance        NPX  
52895                            NEQEQPLGQWHLS           12423.9    12423.9  
52896                              GNPEPTFSWTK          104155.0   605605.0  
52897                          IEIPSSVQQVPTIIK          114454.0   605605.0  
52898   KPQSAVYSTGSNGILLC(UniMod_4)EAEGEPQPTIK           24907.2   605605.0  
52899                             SMEQNGPGLEYR           35356.3   605605.0  
...                                        ...               ...        ...  
645363              EILSVDC(UniMod_4)STNNPSQAK          251923.0  8338150.0  
645364                              EIQNAVNGVK          152618.0  8338150.0  
645365                     FM(UniMod_35)ETVAEK           86861.3  8338150.0  
645366                                FMETVAEK         1581860.0  8338150.0  
645367                                     NaN               NaN        NaN  

[4361 rows x 7 columns]

In [ ]:
train_ProPep.describe()

visit_month     patient_id  PeptideAbundance           NPX
count  645368.000000  645368.000000      6.453670e+05  6.453670e+05
mean       12.265253   31483.786689      6.456508e+05  1.709735e+07
std        10.849952   18610.170269      3.402093e+06  6.352091e+07
min         0.000000      55.000000      1.099850e+01  1.284420e+02
25%         0.000000   15590.000000      2.811020e+04  2.426040e+05
50%        12.000000   27872.000000      7.421080e+04  9.904370e+05
75%        24.000000   49239.000000      2.215095e+05  3.729410e+06
max        36.000000   65043.000000      1.787520e+08  6.138510e+08

In [ ]:
from pandas_profiling import ProfileReport

profile_train_ProPep = ProfileReport(train_ProPep)
profile_train_ProPep.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
train_ProPep_agg = train_ProPep.groupby('visit_id').mean()
train_all = train_clinical_data.merge(train_ProPep_agg[['PeptideAbundance','NPX']],on='visit_id',how='left')
train_all.head()

<ipython-input-21-ab300eb33330>:1: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  train_ProPep_agg = train_ProPep.groupby('visit_id').mean()


visit_id  patient_id  visit_month  updrs_1  updrs_2  updrs_3  updrs_4  \
0     55_0          55            0     10.0      6.0     15.0      NaN   
1     55_3          55            3     10.0      7.0     25.0      NaN   
2     55_6          55            6      8.0     10.0     34.0      NaN   
3     55_9          55            9      8.0      9.0     30.0      0.0   
4    55_12          55           12     10.0     10.0     41.0      0.0   

  upd23b_clinical_state_on_medication  PeptideAbundance           NPX  
0                                 NaN     748153.907014  2.028789e+07  
1                                 NaN               NaN           NaN  
2                                 NaN     685218.599872  1.843914e+07  
3                                  On               NaN           NaN  
4                                  On     740535.423563  2.010976e+07

In [ ]:
profile_train_all = ProfileReport(train_all)
profile_train_all.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]